In [33]:
import pandas as pd
import numpy as np

from scipy.integrate import quad
from scipy.optimize import minimize


from multiprocessing import Pool
from functools import partial
import time
from datetime import datetime

from typing import Dict

import json
import logging
import sys

In [34]:
sep = '######################################################'

config = json.load(open('config/likelihood_ratio_config.json'))

config['df'] = df

grid_size = config['grid_sizes'][0]

sample = json.load(open('data/snls_snia.json'))

df = pd.DataFrame(sample)

In [35]:
def Dc(z: float, Omega_l: float, Omega_m: float, w: float) -> float:
    """
    Calculates the adimensional comoving distance using the input parameters.

    Parameters:
        z (float): The redshift value.
        Omega_l (float): The value of the cosmological constant.
        Omega_m (float): The value of the matter density parameter.
        w (float): The value of the dark energy equation of state.

    Returns:
        The adimensional comoving distance.
        
    Notes:
        The adimensional comoving distance is the distance that would be traveled 
        by a photon emitted at redshift z, if the universe were not expanding, 
        divided by the Hubble distance. This function calculates the comoving 
        distance by performing a numerical integration of the function f(z, Omega_l, 
        Omega_m, w) over the redshift range [0, z], where f(z, Omega_l, Omega_m, w) 
        is defined as:

        f(z, Omega_l, Omega_m, w) = 1 / sqrt(Omega_l*(1 + z)**(3 + 3*w) + 
                                              Omega_m*(1 + z)**3 + 
                                              Omega_k*(1 + z)**2 + 
                                              9.2e-5*(1 + z)**4)

        where Omega_k = 1 - (Omega_l + Omega_m + 9.2e-5) represents the curvature of 
        the universe. The result is returned as an adimensional quantity, which 
        can be converted to physical units of length by multiplying by the Hubble 
        distance.
    """
    
    Omega_k = 1 - (Omega_l + Omega_m + 9.2e-5)

    def f(z, Omega_l, Omega_m, w):
        return 1/(np.sqrt(Omega_l*(1 + z)**(3 + 3*w) + Omega_m*(1 + z)**3 + Omega_k*(1 + z)**2 + 9.2e-5*(1 + z)**4))
    
    result = quad(f, 0, z, args = (Omega_l, Omega_m, w))[0]

    return result

def Dt(z: float, Omega_l: float, Omega_m: float, w: float) -> float:
    """
    Calculates the temporal comoving distance using the input parameters.

    Parameters:
        z (float): The redshift value.
        Omega_l (float): The value of the cosmological constant.
        Omega_m (float): The value of the matter density parameter.
        w (float): The value of the dark energy equation of state.

    Returns:
        The temporal comoving distance.
        
    Notes:  
        -If Omega_k is greater than 0, the universe is positively curved like a 
        sphere, and the correction factor involves a sine function.

        -If Omega_k is equal to 0, the universe is flat, and no correction factor 
        is necessary.

        -If Omega_k is less than 0, the universe is negatively curved like a saddle, 
        and the correction factor involves a hyperbolic sine function.
    """
    
    Omega_k = 1 - (Omega_l + Omega_m + 9.2e-5) # Omega_l + Omega_m + Omega_r + Omega_k = 1
    
    if Omega_k > 0:
        return np.sin(np.sqrt(Omega_k)*Dc(z, Omega_l, Omega_m, w))/np.sqrt(Omega_k)
    elif Omega_k == 0:
        return Dc(z, Omega_l, Omega_m, w)
    elif Omega_k:
        return np.sinh(np.sqrt(abs(Omega_k))*Dc(z, Omega_l, Omega_m, w))/np.sqrt(abs(Omega_k))

def Dl(z: float, Omega_l: float, Omega_m: float, w: float) -> float:
    """
    Calculates the luminosity distance using the input parameters.

    Parameters:
        z (float): The redshift value.
        Omega_l (float): The value of the cosmological constant.
        Omega_m (float): The value of the matter density parameter.
        w (float): The value of the dark energy equation of state.

    Returns:
        The luminosity distance.
    """
    
    return (1 + z) * Dt(z, Omega_l, Omega_m, w)
               
def mu(z: float, Omega_l: float, Omega_m: float, w: float, Hubble: float) -> float:
    """
    Calculates the distance modulus using the input parameters.

    Parameters:
        z (float): The redshift value.
        Omega_l (float): The value of the cosmological constant.
        Omega_m (float): The value of the matter density parameter.
        w (float): The value of the dark energy equation of state.
        Hubble (float): The Hubble parameter.

    Returns:
        The distance modulus.
    """
    
    c = 3e5 #(km/s)
    return 5*np.log10(Dl(z, Omega_l, Omega_m, w)) + 25 + 5*np.log10(c/ Hubble)

def chi2_i(mu_o: float, sigma_o: float, z_obs: float, Omega_l: float, Omega_m: float, w: float, Hubble: float) -> float:
    """
    Calculates the chi-squared value for a single data point using the input parameters.

    Parameters:
        mu_o (float): The observed distance modulus.
        sigma_o (float): The uncertainty in the observed distance modulus.
        z_obs (float): The observed redshift value.
        Omega_l (float): The value of the cosmological constant.
        Omega_m (float): The value of the matter density parameter.
        w (float): The value of the dark energy equation of state.
        Hubble (float): The Hubble parameter.

    Returns:
        The chi-squared value for a single data point.
    """
    
    _mu = mu(z_obs, Omega_l, Omega_m, w, Hubble)
    print('In chi2_i func: ', mu_o, _mu, Omega_l, Omega_m, w, Hubble)
    return ((_mu - mu_o)**2)/sigma_o**2

def chi2(Omega_l: float, Omega_m: float, w: float, Hubble: float, df): 
    """
    Calculates the chi-squared value for a set of data points using the input parameters.

    Parameters:
        Omega_l (float): The value of the cosmological constant.
        Omega_m (float): The value of the matter density parameter.
        w (float): The value of the dark energy equation of state.
        Hubble (float): The Hubble parameter.
        df (pandas.DataFrame): The dataframe containing the observed redshift values, distance moduli, and uncertainties.

    Returns:
        The chi-squared value for the set of data points.
    """
    values = []
    print(sep)
    print('Before for: ', Omega_l, Omega_m, w, Hubble)
    for idx in df.index:
        print('In for: ', Omega_l, Omega_m, w, Hubble)
        values.append(chi2_i(df.mu[idx], df.sigma[idx], df.z[idx], Omega_l, Omega_m, w, Hubble))
    result = sum(values)
    return result

def ratio(Omega_l: float, Omega_m: float, w: float, Hubble: float, df, chi2null: float) -> float:
    """
    Calculates the likelihood ratio test statistic for a given set of cosmological
    parameters and data.

    Parameters:
        Omega_l (float): The cosmological constant.
        Omega_m (float): The density of matter.
        w (float): The dark energy equation of state parameter.
        Hubble (float): The Hubble constant in units of km/s/Mpc.
        df (pandas.DataFrame): A DataFrame with columns for redshift (z), observed
            distance modulus (mu_o), and uncertainty (sigma_o).
        chi2null (float): The chi-squared value for the null model, i.e., the chi-
            squared value for the observed data using the values of the cosmological
            parameters in the null hypothesis.

    Returns:
        float: The difference in chi-squared values between the null and alternative
            models.
    """
    
    return chi2(Omega_l, Omega_m, w, Hubble, df) - chi2null

In [36]:
def cartesian_product(*linspaces):
    """
    Compute the cartesian product of a set of one-dimensional arrays.

    Given n one-dimensional arrays, this function returns an array of shape (N, n), where
    N is the product of the lengths of the input arrays. The resulting array is obtained 
    by taking the Cartesian product of the input arrays, with the first array varying 
    fastest and the last array varying slowest.

    Args:
        *linspaces: One or more one-dimensional arrays to be used in the cartesian product.

    Returns:
        A 2D numpy array of shape (N, n), where N is the product of the lengths of the 
        input arrays, and n is the number of input arrays. The i-th row of the array 
        contains the i-th combination of values from the input arrays.
    """
    
    # Create a list to hold the linspaces and their lengths
    linspaces_list = []
    lengths = []

    # Loop through each linspace and get its values and length
    for linspace in linspaces:
        linspaces_list.append(linspace)
        lengths.append(len(linspace))

    # Create a 2D array to hold the cartesian product
    cartesian_product_array = np.zeros((np.prod(lengths), len(linspaces)))

    # Loop through each value in the linspaces and add it to the cartesian product array
    for i in range(len(linspaces)):
        repeat = np.prod(lengths[i+1:])
        cartesian_product_array[:, i] = np.tile(np.repeat(linspaces[i], repeat), np.prod(lengths[:i]))

    return cartesian_product_array

def _zip_vars(fixed: dict, x) -> dict:
    """
    Given a dictionary of fixed parameters and an array of values, this function creates 
    an ordered dictionary estimating the position of each value in the array for the 
    remaining unfixed parameters (in the order Omega_l, Omega_m, w, and Hubble). 

    Args:
        fixed (dict): A dictionary of fixed parameters.
        x: An array of values with length equal to the number of unfixed parameters.

    Returns:
        A dictionary with keys corresponding to unfixed parameters and values corresponding 
        to the corresponding values in x.
    """
    
    full_parameters = ['Omega_l', 'Omega_m', 'w', 'Hubble']
    variable_parameters = [param for param in full_parameters if param not in fixed]
    _vars = dict(zip(variable_parameters, x))
    
    return _vars

def h(x, fixed: dict, df) -> float:
    """
    A wrapper for the chi2 function that enables minimize to pass an array of arguments 
    by creating a dictionary of variables to be optimized. 

    Args:
        x: An array of values to be optimized.
        fixed (dict): A dictionary of fixed variables.
        df: A pandas dataframe containing the data to be fitted.

    Returns:
        The value of the chi-squared function for the given parameters.
    """
    
    print(f"Params passed by the optimization method: {x}")
    # Creates dictionary of variables to be optimized
    _vars = _zip_vars(fixed, x)

    g = partial(chi2, df=df, **fixed) # Creates partial function fixing variables set by `fixed`
    # Unzips `_vars` as named args to `g`
    return g(**_vars) 

In [40]:
def _minimize(args: tuple):
    """
    Minimizes the given function h using the Nelder-Mead method and returns the optimal value of x.

    Parameters:
        args (tuple): A tuple containing the values of the arguments to be passed to the function h.

    Returns:
        x (array): The optimal value of x that minimizes the function h.
    """
    
    dict_kwargs = {
        'fun': h,
        'x0': args[2],
        'args': (args[0], args[1]),
        'method': 'Nelder-Mead',
        'jac': None,
        'hessp': None,
        'hess': None,
        'constraints': (),
        'tol': 1e-3,
        'callback': None,
        'options': None,
    }
    _min = minimize(**dict_kwargs)
    return _min.x

def generate_grid(config, grid_size):
    """
    Generates a grid of values for the given configuration and grid size, and finds the optimal values of the free parameters
    using the _minimize function.

    Parameters:
        config (dict): A dictionary containing the configuration for the grid search.
        grid_size (int): The size of the grid to be generated.

    Yields:
        result (tuple): The optimal value of x that minimizes the function h for the current set of free parameters.
    """    
    def generate_free_params(config, grid_size):
        standard_x0 = {'Omega_l':0.74, 'Omega_m':0.26, 'w':-1,  'Hubble':70}
        linspaces = []
        for free in config['free']:
            linspaces.append(np.linspace(config['grid'][free][0], config['grid'][free][1], grid_size))
        cartesian = cartesian_product(*linspaces)
        for i in cartesian:

            fixed = {config['free'][j]: i[j] for j in range(len(config['free']))}
            dict1 = {key: value for key, value in standard_x0.items() if key not in fixed}
            standard_x0_values = [value for value in dict1.values()]

            yield fixed, config['df'], standard_x0_values
    
    
    with Pool() as pool:
        results = pool.map(_minimize, generate_free_params(config, grid_size))
        pool.close()
        pool.join()

    for result in results:
        yield  result

In [41]:
# Optimizing every variable to find null hypothesis

x0 = [0.76, 0.24, -1, 71] #['Omega_l', 'Omega_m', 'w',  'Hubble']
minimum = minimize(h, x0 = x0, args = ({}, df), method = 'Nelder-Mead', tol = 1e-6, bounds = ((0,1), (0,1), (None, None), (0,None)), options = {'maxiter': 10000})

Params passed by the optimization method: [ 0.76  0.24 -1.   71.  ]
######################################################
Before for:  0.76 0.24 -1.0 71.0
In for:  0.76 0.24 -1.0 71.0
In chi2_i func:  34.11747 34.09832480009925 0.76 0.24 -1.0 71.0
In for:  0.76 0.24 -1.0 71.0
In chi2_i func:  34.08234 34.161531660323725 0.76 0.24 -1.0 71.0
In for:  0.76 0.24 -1.0 71.0
In chi2_i func:  34.07026 34.198611969086954 0.76 0.24 -1.0 71.0
In for:  0.76 0.24 -1.0 71.0
In chi2_i func:  34.40483 34.22029767494338 0.76 0.24 -1.0 71.0
In for:  0.76 0.24 -1.0 71.0
In chi2_i func:  34.12864 34.23910104786756 0.76 0.24 -1.0 71.0
In for:  0.76 0.24 -1.0 71.0
In chi2_i func:  34.45123 34.26039811716748 0.76 0.24 -1.0 71.0
In for:  0.76 0.24 -1.0 71.0
In chi2_i func:  34.3188 34.28935325964008 0.76 0.24 -1.0 71.0
In for:  0.76 0.24 -1.0 71.0
In chi2_i func:  34.21556 34.338497827497676 0.76 0.24 -1.0 71.0
In for:  0.76 0.24 -1.0 71.0
In chi2_i func:  34.16124 34.35506492371567 0.76 0.24 -1.0 71.0
In fo

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



Params passed by the optimization method: [ 0.56626896  0.         -1.06862288 70.11758214]
######################################################
Before for:  0.5662689557977845 0.0 -1.0686228809829443 70.11758213758634
In for:  0.5662689557977845 0.0 -1.0686228809829443 70.11758213758634
In chi2_i func:  34.11747 34.12520693609598 0.5662689557977845 0.0 -1.0686228809829443 70.11758213758634
In for:  0.5662689557977845 0.0 -1.0686228809829443 70.11758213758634
In chi2_i func:  34.08234 34.18840530003227 0.5662689557977845 0.0 -1.0686228809829443 70.11758213758634
In for:  0.5662689557977845 0.0 -1.0686228809829443 70.11758213758634
In chi2_i func:  34.07026 34.2254804982927 0.5662689557977845 0.0 -1.0686228809829443 70.11758213758634
In for:  0.5662689557977845 0.0 -1.0686228809829443 70.11758213758634
In chi2_i func:  34.40483 34.24716317120285 0.5662689557977845 0.0 -1.0686228809829443 70.11758213758634
In for:  0.5662689557977845 0.0 -1.0686228809829443 70.11758213758634
In chi2_i 

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In chi2_i func:  42.03744 42.0221880392869 0.56190225258802 5.6461735964982615e-05 -1.1000094173226733 70.15507232788721
In for:  0.56190225258802 5.6461735964982615e-05 -1.1000094173226733 70.15507232788721
In chi2_i func:  42.03011 42.07768255357381 0.56190225258802 5.6461735964982615e-05 -1.1000094173226733 70.15507232788721
In for:  0.56190225258802 5.6461735964982615e-05 -1.1000094173226733 70.15507232788721
In chi2_i func:  42.08907 42.088989547733405 0.56190225258802 5.6461735964982615e-05 -1.1000094173226733 70.15507232788721
In for:  0.56190225258802 5.6461735964982615e-05 -1.1000094173226733 70.15507232788721
In chi2_i func:  42.26791 42.1298778260515 0.56190225258802 5.6461735964982615e-05 -1.1000094173226733 70.15507232788721
In for:  0.56190225258802 5.6461735964982615e-05 -1.1000094173226733 70.15507232788721
In chi2_i func:  42.17991 42.27085189038381 0.56190225258802 5.6461735964982615e-05 -1.1000094173226733 70.15507232788721
In for:  0.56190225258802 5.646173596498261

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [38]:
type(minimum.x)

numpy.ndarray